<a target="_blank" href="https://colab.research.google.com/github/EasyScience/EasyDiffractionLib/blob/new_job_dev2/examples/Fitting_PD-TOF_Si-SEPD@Argonne/fitting.ipynb">
  <img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/>
</a>

# Fitting TOF-PD

This example shows how to refine the crystal structure parameters of Si from neutron diffraction data in a time-of-flight experiment performed on SEPD diffractometer at Argonne.

## Import

In [16]:
# Google Colab related imports
import os
import importlib.util

if os.getenv("COLAB_RELEASE_TAG"):
   print("Running in Google Colab")
   # Install the easydiffraction library if it is not installed (including charts extras)
   if importlib.util.find_spec("easydiffraction") is None:
       !pip install 'easydiffraction[charts] @ git+https://github.com/easyscience/easydiffractionlib.git@new_job_dev2'
   # Download the data files to be read in notebook
   if not os.path.exists('si.cif'):
       !wget https://raw.githubusercontent.com/EasyScience/EasyDiffractionLib/refs/heads/new_job_dev/examples/Fitting_PD-TOF_Si-SEPD@Argonne/si.cif
   if not os.path.exists('sepd.xye'):
       !wget https://raw.githubusercontent.com/EasyScience/EasyDiffractionLib/refs/heads/new_job_dev/examples/Fitting_PD-TOF_Si-SEPD@Argonne/sepd.xye

In [17]:
# Import the easydiffraction library
import easydiffraction as ed

## Job

In [18]:
# Create a job - the main object to store all the information
job = ed.Job(type='tof')

## Model

In [19]:
# Load a phase from CIF file
job.add_phase_from_file('si.cif')
print(job.phases)

Several values of it_coordinate_system_code have been defined:
2, 1
The default value has been choosen:'2'.
Several values of it_coordinate_system_code have been defined:
2, 1
The default value has been choosen:'2'.
Collection of 1 phases: ['si']


In [20]:
# Show phase info in CIF format
phase = job.phases['si']
print(phase.cif)

data_si
_cell_length_a 5.43146
_cell_length_b 5.43146
_cell_length_c 5.43146
_cell_angle_alpha 90.00000000
_cell_angle_beta 90.00000000
_cell_angle_gamma 90.00000000
_space_group_name_H-M_ref 'F d -3 m'
_space_group_IT_coordinate_system_code 1

loop_
_atom_site_label
_atom_site_type_symbol
_atom_site_fract_x
_atom_site_fract_y
_atom_site_fract_z
_atom_site_occupancy
_atom_site_adp_type
_atom_site_B_iso_or_equiv
Si Si 0.125 0.125 0.125 1.00000000 Biso 0.529


In [21]:
# Display the crystal structure of a given model
job.show_crystal_structure(id='si')

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

## Experiment

In [22]:
# Load experimentally measured data from a file in XYE format
job.add_experiment_from_file('sepd.xye')

In [23]:
pattern_params = job.pattern
experiment_params = job.parameters

In [24]:
job.show_experiment_chart()

## Analysis

In [25]:
# Display the analysis chart before setting initial parameter values
job.show_analysis_chart()

In [42]:
# Modify model-related parameters
phase.scale = 10
phase.cell.length_a = 5.43

# Modify experiment-related parameters
pattern_params.zero_shift = 0

experiment_params.dtt1 = 7476.91
experiment_params.dtt2 = -1.54
experiment_params.ttheta_bank = 144.845

experiment_params.alpha0 = 0.024
experiment_params.alpha1 = 0.204
experiment_params.beta0 = 0.038
experiment_params.beta1 = 0.011
experiment_params.sigma0 = 0.01
experiment_params.sigma1 = 0.01
experiment_params.sigma2 = 0.01

job.set_background([( 2000.0, 221.1),
                    ( 4000.0, 169.5),
                    ( 6000.0, 135.4),
                    (10000.0, 121.4),
                    (14000.0, 132.2),
                    (18000.0, 134.0),
                    (22000.0, 143.0),
                    (25000.0, 183.0),
                    (28000.0, 165.0),
                    (29995.0, 204.0)])

In [43]:
# Display the analysis chart after modifying parameters
job.show_analysis_chart()

In [44]:
# Select the model-related parameters to be fitted
phase.scale.free = True
phase.cell.length_a.free = True

# Select the experiment-related parameters to be fitted
pattern_params.zero_shift.free = True

experiment_params.sigma0.free = True
experiment_params.sigma1.free = True
experiment_params.sigma2.free = True

In [45]:
# Print parameters before fitting
job.print_free_parameters()

<Parameter 'length_a': 5.430000+/-0.000024 Å, bounds=[0:inf]>
<Parameter 'scale': 10.000+/-0.020, bounds=[0:inf]>
<Parameter 'sigma0': 0.0+/-0.9, bounds=[-inf:inf]>
<Parameter 'sigma1': 0.0+/-0.7, bounds=[-inf:inf]>
<Parameter 'sigma2': 0.01+/-0.08, bounds=[-inf:inf]>
<Parameter 'zero_shift': 0.000+/-0.032 µs, bounds=[-inf:inf]>


In [46]:
%%time
# Start Least-Squares minimization to fit the selected parameters
#job.fit(method='leastsq', tolerance=1e-5)
job.analysis.current_minimizer = 'LMFit_leastsq'
#job.analysis.current_minimizer = 'Bumps_simplex'
job.fit()

*** fit results:
[[Fit Statistics]]
    # fitting method   = leastsq
    # function evals   = 50
    # data points      = 5600
    # variables        = 6
    chi-square         = 29664.0890
    reduced chi-square = 5.30284037
    Akaike info crit   = 9348.15532
    Bayesian info crit = 9387.93845
    R-squared          = 0.99999424
[[Variables]]
    pParameter_110:  5.43194446 +/- 5.1381e-05 (0.00%) (init = 5.43)
    pParameter_116:  14.8785660 +/- 0.04568640 (0.31%) (init = 10)
    pParameter_89:   4.51279862 +/- 1.41395069 (31.33%) (init = 0.01)
    pParameter_90:   28.1175617 +/- 1.65407281 (5.88%) (init = 0.01)
    pParameter_91:   1.01539602 +/- 0.18032701 (17.76%) (init = 0.01)
    pParameter_117: -3.94690350 +/- 0.06730294 (1.71%) (init = 0)
[[Correlations]] (unreported correlations are < 0.100)
    C(pParameter_90, pParameter_91)   = -0.9367
    C(pParameter_110, pParameter_117) = -0.8672
    C(pParameter_89, pParameter_90)   = -0.6800
    C(pParameter_89, pParameter_91)   = +0

In [47]:
# Print parameters after fitting
job.print_free_parameters()

<Parameter 'length_a': 5.43194+/-0.00005 Å, bounds=[0:inf]>
<Parameter 'scale': 14.88+/-0.05, bounds=[0:inf]>
<Parameter 'sigma0': 4.5+/-1.4, bounds=[-inf:inf]>
<Parameter 'sigma1': 28.1+/-1.7, bounds=[-inf:inf]>
<Parameter 'sigma2': 1.02+/-0.18, bounds=[-inf:inf]>
<Parameter 'zero_shift': -3.95+/-0.07 µs, bounds=[-inf:inf]>


In [48]:
job.print_free_parameters()

<Parameter 'length_a': 5.43194+/-0.00005 Å, bounds=[0:inf]>
<Parameter 'scale': 14.88+/-0.05, bounds=[0:inf]>
<Parameter 'sigma0': 4.5+/-1.4, bounds=[-inf:inf]>
<Parameter 'sigma1': 28.1+/-1.7, bounds=[-inf:inf]>
<Parameter 'sigma2': 1.02+/-0.18, bounds=[-inf:inf]>
<Parameter 'zero_shift': -3.95+/-0.07 µs, bounds=[-inf:inf]>


In [49]:
# Display the analysis chart after fitting
job.show_analysis_chart()